In [1]:
import pyvista as pv
import numpy as np
import xarray as xr

from ipygany import PolyMesh, Scene, IsoColor, WarpByScalar, ColorBar, colormaps
from ipywidgets import VBox, FloatSlider, FileUpload, Dropdown, jslink, FloatRangeSlider, AppLayout


In [2]:
ds = xr.open_dataset('/home/climwork/psepul/BC_CM5A2/DATASET_Straume_et_al_2020/Paleobathymetry-paleotopography/paleobathy-topo_55.00Ma_Straume_et_al_1x1.nc')
ds

<xarray.Dataset>
Dimensions:  (lat: 180, lon: 360)
Coordinates:
  * lon      (lon) float64 0.0 1.0 2.0 3.0 4.0 ... 355.0 356.0 357.0 358.0 359.0
  * lat      (lat) float64 -89.5 -88.5 -87.5 -86.5 -85.5 ... 86.5 87.5 88.5 89.5
Data variables:
    TOPO     (lat, lon) float32 ...
Attributes:
    CDI:          Climate Data Interface version 1.9.9 (https://mpimet.mpg.de...
    Conventions:  COARDS, CF-1.5
    GMT_version:  5.4.5 [64-bit]
    history:      Thu Feb 04 16:14:31 2021: cdo remapbil,r360x180 paleobathy-...
    NCO:          netCDF Operators version 4.9.7 (Homepage = http://nco.sf.ne...
    CDO:          Climate Data Operators version 1.9.9 (https://mpimet.mpg.de...

In [3]:
xx, yy, zz = np.meshgrid(np.radians(ds['lon']), 
                         np.radians(ds['lat']), 
                         [0])

# Transform to spherical coordinates
radius = 6371.0e6
x = radius * np.cos(yy) * np.cos(xx)
y = radius * np.cos(yy) * np.sin(xx)
z = radius * np.sin(yy)

grid = pv.StructuredGrid(x, y, z)

# Add data to mesh
for var in ds.data_vars:
    grid[var] = np.array(ds[var]).ravel(order='F')


## Convert pyvista mesh to ipygany mesh

In [4]:
# Turn the PyVista mesh into a PolyMesh
mesh = PolyMesh.from_vtk(grid)

# Color the mesh
#colored_mesh = IsoColor(mesh, min=ds.TOPO.min(), max=ds.TOPO.max())
### Get min/max values of the variable
topo_min = ds.TOPO.min()
topo_max = ds.TOPO.max()

# Colorize by height
colored_mesh = IsoColor(mesh, min=topo_min, max=topo_max)



In [5]:

# setup warping
warped_mesh = WarpByScalar(colored_mesh, input='TOPO', factor=0)

# Create a slider that will dynamically change the boundaries of the colormap
colormap_slider_range = FloatRangeSlider(value=[topo_min, topo_max], min=topo_min, max=topo_max, step= 100.)
jslink((colored_mesh, 'range'), (colormap_slider_range, 'value'))

# Link a slider to the warp value
warp_slider = FloatSlider(min=0., max=10., value=0)

def on_slider_change(change):
    warped_mesh.factor = change['new'] * -1e4

warp_slider.observe(on_slider_change, 'value')

# Create a colorbar widget
colorbar = ColorBar(colored_mesh)

# Colormap choice widget
colormap = Dropdown(
    options=colormaps,
    description='colormap:'
)

jslink((colored_mesh, 'colormap'), (colormap, 'index'))


AppLayout(
    left_sidebar=Scene([warped_mesh]),
    right_sidebar=VBox((warp_slider,colormap_slider_range, colormap, colorbar)),
    pane_widths=[2, 0, 1]
)

AppLayout(children=(Scene(children=[WarpByScalar(factor=0.0, input='TOPO', parent=IsoColor(input='TOPO', max=6…